<a href="https://colab.research.google.com/github/sipocz/CabPrice/blob/B20210522/CabPrice_MLPregressor.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [348]:
!wget https://github.com/sipocz/CabPrice/raw/B20210507/TRAIN.csv

--2021-05-22 14:06:13--  https://github.com/sipocz/CabPrice/raw/B20210507/TRAIN.csv
Resolving github.com (github.com)... 140.82.113.4
Connecting to github.com (github.com)|140.82.113.4|:443... connected.
HTTP request sent, awaiting response... 302 Found
Location: https://raw.githubusercontent.com/sipocz/CabPrice/B20210507/TRAIN.csv [following]
--2021-05-22 14:06:13--  https://raw.githubusercontent.com/sipocz/CabPrice/B20210507/TRAIN.csv
Resolving raw.githubusercontent.com (raw.githubusercontent.com)... 185.199.108.133, 185.199.111.133, 185.199.109.133, ...
Connecting to raw.githubusercontent.com (raw.githubusercontent.com)|185.199.108.133|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 7524003 (7.2M) [text/plain]
Saving to: ‘TRAIN.csv.9’

TRAIN.csv.9         100%[===================>]   7.17M  --.-KB/s    in 0.09s   

2021-05-22 14:06:14 (84.0 MB/s) - ‘TRAIN.csv.9’ saved [7524003/7524003]



In [349]:
!head TRAIN.csv

index,time_stamp,cab_provider,source,destination,distance,surge_multiplier,cab_type,fare
0,1543203646318,Lyft,Boston University,Theatre District,3.03,1.0,Lux Black XL,34.0
1,1543203646319,Uber,South Station,Theatre District,1.3,1.0,Black,18.5
2,1543203646320,Uber,Theatre District,Fenway,2.71,1.0,UberX,19.5
3,1543203646320,Lyft,Northeastern University,Beacon Hill,2.43,1.0,Lyft,10.5
4,1543203646320,Uber,Theatre District,Fenway,2.71,1.0,UberXL,32.0
5,1543203646358,Uber,Beacon Hill,North End,2.19,1.0,UberX,8.0
6,1543203646358,Uber,North Station,Fenway,3.05,1.0,WAV,10.5
7,1543203646358,Uber,Beacon Hill,North End,2.19,1.0,UberXL,13.0
8,1543203646358,Uber,Beacon Hill,North End,2.19,1.0,Black,17.5


In [350]:
import pandas as pd
import numpy as np

sources['source_Back Bay'],sources['source_Beacon Hill'],sources['source_Boston University'],
                    sources['source_Fenway'],sources['source_Financial District'],sources['source_Haymarket Square'],
                    sources['source_North End'],sources['source_North Station'],sources['source_Northeastern University'],
                    sources['source_South Station'],sources['source_Theatre District'],sources['source_West End'],
                     
                    dest['dest_Back Bay'],dest['dest_Beacon Hill'],dest['dest_Boston University'],
                    dest['dest_Fenway'],dest['dest_Financial District'],dest['dest_Haymarket Square'],
                    dest['dest_North End'],dest['dest_North Station'],dest['dest_Northeastern University'],
                    dest['dest_South Station'],dest['dest_Theatre District'],dest['dest_West End'],

                       ''' 
                    cabtype['cab_type_Black'],cabtype['cab_type_Black SUV'],cabtype['cab_type_Lux'],cabtype['cab_type_Lux Black'],
                    cabtype['cab_type_Lux Black XL'],cabtype['cab_type_Lyft'],cabtype['cab_type_Lyft XL'],cabtype['cab_type_Shared'],
                    cabtype['cab_type_UberPool'],cabtype['cab_type_UberX'],cabtype['cab_type_UberXL'],cabtype['cab_type_WAV'],
                    #dow["dow_0"],dow["dow_1"],dow["dow_2"],
                    '''   


In [351]:
def DataPipeLine(df, startup=True):
    #outlierek 
    if startup:
        df["price_per"]=df.fare/df.surge_multiplier/df.distance
        df.drop(df[df['price_per'] > 73].index, inplace = True)
        #df.drop(df[df.cab_provider=="Lyft"].index, inplace=True)
    
    df["sec"]=(df.time_stamp/1000) % (24*3600)
    seconds_in_day = 24*60*60
    df['sin_time'] = (np.sin(2*np.pi*df.sec/seconds_in_day))
    df['cos_time'] = (np.cos(2*np.pi*df.sec/seconds_in_day))

    sources=pd.get_dummies(df["source"],prefix='source',drop_first=False)
    dest=pd.get_dummies(df["destination"],prefix='dest',drop_first=False)
    cab=pd.get_dummies(df["cab_provider"],prefix='provider',drop_first=False)
    
    a=df.time_stamp
    df["DateTime"]=a.apply( lambda x:pd.Timestamp(x,unit="ms"))
    #df["dow"]=df["DateTime"].dt.dayofweek
    
    #dow=pd.get_dummies(df["dow"],prefix='dow',drop_first=False)


    sources=pd.get_dummies(df["source"],prefix='source',drop_first=False)
    dest=pd.get_dummies(df["destination"],prefix='dest',drop_first=False)
    cab=pd.get_dummies(df["cab_provider"],prefix='provider',drop_first=False)
    cabtype=pd.get_dummies(df["cab_type"],prefix='cab_type',drop_first=False)

    new = pd.DataFrame([df.DateTime, sources.columns, dest.columns])


    Xret = pd.DataFrame([
                    
                    cab['provider_Lyft'],
                    cab['provider_Uber'],
                    sources['source_Back Bay'],sources['source_Beacon Hill'],sources['source_Boston University'],
                    sources['source_Fenway'],sources['source_Financial District'],sources['source_Haymarket Square'],
                    sources['source_North End'],sources['source_North Station'],sources['source_Northeastern University'],
                    sources['source_South Station'],sources['source_Theatre District'],sources['source_West End'],
                     
                    dest['dest_Back Bay'],dest['dest_Beacon Hill'],dest['dest_Boston University'],
                    dest['dest_Fenway'],dest['dest_Financial District'],dest['dest_Haymarket Square'],
                    dest['dest_North End'],dest['dest_North Station'],dest['dest_Northeastern University'],
                    dest['dest_South Station'],dest['dest_Theatre District'],dest['dest_West End'],

                    cabtype['cab_type_Black'],cabtype['cab_type_Black SUV'],cabtype['cab_type_Lux'],cabtype['cab_type_Lux Black'],
                    cabtype['cab_type_Lux Black XL'],cabtype['cab_type_Lyft'],cabtype['cab_type_Lyft XL'],cabtype['cab_type_Shared'],
                    cabtype['cab_type_UberPool'],cabtype['cab_type_UberX'],cabtype['cab_type_UberXL'],cabtype['cab_type_WAV'],
                    #dow["dow_0"],dow["dow_1"],dow["dow_2"],



                    df["distance"],   # /10,
                    df["surge_multiplier"], #/3,
                    (df["sin_time"]/2)+0.5,
                    (df["cos_time"]/2)+0.5
                    #df.fare/df["surge_multiplier"]/df["distance"],
                    #df.fare
                    ]).transpose()
    return(Xret)



In [352]:
df=pd.read_csv("TRAIN.csv")

In [353]:
df.head()

index     time_stamp cab_provider  ... surge_multiplier      cab_type  fare
0      0  1543203646318         Lyft  ...              1.0  Lux Black XL  34.0
1      1  1543203646319         Uber  ...              1.0         Black  18.5
2      2  1543203646320         Uber  ...              1.0         UberX  19.5
3      3  1543203646320         Lyft  ...              1.0          Lyft  10.5
4      4  1543203646320         Uber  ...              1.0        UberXL  32.0

[5 rows x 9 columns]

In [354]:
X_trainn=DataPipeLine(df)   

In [355]:
df.head()

index     time_stamp  ...  cos_time                DateTime
0      0  1543203646318  ...  0.570814 2018-11-26 03:40:46.318
1      1  1543203646319  ...  0.570814 2018-11-26 03:40:46.319
2      2  1543203646320  ...  0.570814 2018-11-26 03:40:46.320
3      3  1543203646320  ...  0.570814 2018-11-26 03:40:46.320
4      4  1543203646320  ...  0.570814 2018-11-26 03:40:46.320

[5 rows x 14 columns]

In [356]:
X_trainn["surge_multiplier"].max()

3.0

In [357]:
X_trainn.head()

provider_Lyft  provider_Uber  ...  sin_time  cos_time
0            1.0            0.0  ...   0.91054  0.785407
1            0.0            1.0  ...   0.91054  0.785407
2            0.0            1.0  ...   0.91054  0.785407
3            1.0            0.0  ...   0.91054  0.785407
4            0.0            1.0  ...   0.91054  0.785407

[5 rows x 42 columns]

In [358]:
#df.DateTime
(df.time_stamp/1000) % (24*3600)

0        13246.318
1        13246.319
2        13246.320
3        13246.320
4        13246.320
           ...    
99995      924.049
99996      924.049
99997      924.049
99998      924.049
99999      924.049
Name: time_stamp, Length: 99920, dtype: float64

In [359]:
ytrain=df["fare"]

In [360]:
X_trainn

provider_Lyft  provider_Uber  ...  sin_time  cos_time
0                1.0            0.0  ...  0.910540  0.785407
1                0.0            1.0  ...  0.910540  0.785407
2                0.0            1.0  ...  0.910540  0.785407
3                1.0            0.0  ...  0.910540  0.785407
4                0.0            1.0  ...  0.910540  0.785407
...              ...            ...  ...       ...       ...
99995            0.0            1.0  ...  0.533574  0.998872
99996            0.0            1.0  ...  0.533574  0.998872
99997            0.0            1.0  ...  0.533574  0.998872
99998            0.0            1.0  ...  0.533574  0.998872
99999            0.0            1.0  ...  0.533574  0.998872

[99920 rows x 42 columns]

In [365]:

remover=X_trainn[X_trainn.provider_Uber==1].index
X_train_Lyft=X_trainn.drop(remover, inplace=False)
y_trainn=df["fare"]
y_train_Lyft=y_trainn.drop(remover,inplace=False)

remover=X_trainn[X_trainn.provider_Lyft==1].index
X_train_Uber=X_trainn.drop(remover, inplace=False)
y_trainn=df["fare"]
y_train_Uber=y_trainn.drop(remover,inplace=False)





In [366]:
print(y_train_Uber)

1        18.5
2        19.5
4        32.0
5         8.0
6        10.5
         ... 
99995    12.0
99996    26.0
99997    16.0
99998     7.0
99999     7.0
Name: fare, Length: 51783, dtype: float64


In [307]:
X_trainn

provider_Lyft  provider_Uber  ...  sin_time  cos_time
0                1.0            0.0  ...  0.910540  0.785407
3                1.0            0.0  ...  0.910540  0.785407
9                1.0            0.0  ...  0.910541  0.785406
10               1.0            0.0  ...  0.910541  0.785406
11               1.0            0.0  ...  0.910541  0.785406
...              ...            ...  ...       ...       ...
99988            1.0            0.0  ...  0.533570  0.998872
99989            1.0            0.0  ...  0.533572  0.998872
99990            1.0            0.0  ...  0.533572  0.998872
99991            1.0            0.0  ...  0.533572  0.998872
99993            1.0            0.0  ...  0.533572  0.998872

[48137 rows x 42 columns]

In [308]:
!rm visual_view.py
!wget https://raw.githubusercontent.com/sipocz/messer/main/visual_view.py
grafikon=None
from visual_view import grafikon
help(grafikon)

--2021-05-22 13:55:45--  https://raw.githubusercontent.com/sipocz/messer/main/visual_view.py
Resolving raw.githubusercontent.com (raw.githubusercontent.com)... 185.199.108.133, 185.199.109.133, 185.199.110.133, ...
Connecting to raw.githubusercontent.com (raw.githubusercontent.com)|185.199.108.133|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 1027 (1.0K) [text/plain]
Saving to: ‘visual_view.py’

visual_view.py      100%[===================>]   1.00K  --.-KB/s    in 0s      

2021-05-22 13:55:46 (45.1 MB/s) - ‘visual_view.py’ saved [1027/1027]

Help on function grafikon in module visual_view:

grafikon(fx, desc1, txt1, desc2='', txt2='', ngraf=2, c1='rgba(35,128,132,0.8)', c2='rgba(193,99,99,0.8)', title=None)
    fx: dataFrame
    desc1:column1
    txt1: label1
    desc2:column2
    txt2: label2
    ngraf: number of graph
    c1: color1
    c2: color2
    title: graph title



In [309]:
df["t_sec"]=(df["time_stamp"]-(df["time_stamp"]%100)) 

In [310]:
aa=list((df["t_sec"]))
print(len(aa))

99920


In [311]:
df.index=df.DateTime

In [312]:
df["price_per"]=df.fare/df.surge_multiplier/df.distance

In [313]:
grafikon(df,"price_per","price_per",ngraf=1)

##szedjuk ki a 100-nál nagyobb sorokat

In [314]:
from keras.layers import InputLayer, Dense, LSTM, Input, Dropout,Embedding, Flatten
from keras.models import Sequential, Model
from keras.optimizers import SGD,Adam,Adamax,Nadam,Ftrl,Adadelta,Adagrad,Nadam
import tensorflow as tf
from tensorflow.keras.callbacks import ModelCheckpoint
from keras.backend import clear_session
from tensorflow.keras.losses import mean_absolute_percentage_error, huber,kld,mse

from keras.preprocessing.sequence import pad_sequences

In [315]:
fname="_model_1_"

In [316]:
'''
from sklearn.ensemble import IsolationForest
iso = IsolationForest(contamination=0.01)
yhat = iso.fit_predict(X_trainn)
'''

'\nfrom sklearn.ensemble import IsolationForest\niso = IsolationForest(contamination=0.01)\nyhat = iso.fit_predict(X_trainn)\n'

In [317]:
clear_session()




input_len=len(X_trainn.columns)
print(input_len)
output_size=1
drop_frac0=0.7 
drop_frac1=0.3



input1=Input(shape=(input_len,),)


#flatt=Flatten()(lstm1)

non=42
#initializer = tf.keras.initializers.LecunNormal()
initializer=tf.keras.initializers.LecunUniform()
#initializer=tf.keras.initializers.HeUniform(    seed=None)
#initializer= tf.keras.initializers.RandomNormal(    mean=1.0, stddev=0.05, seed=None)

d1=Dense(5600,activation="swish",kernel_initializer=initializer)(input1)
drop0=Dropout(drop_frac0)(d1)

'''
d2=Dense(600,activation="swish",)(drop0)
drop1=Dropout(drop_frac0)(d2)
'''


pred=Dense(output_size,activation="linear")(drop0)

model = Model(inputs=input1, outputs=pred)

opt = tf.keras.optimizers.Adam(learning_rate=0.00001)


rmse = tf.keras.metrics.RootMeanSquaredError()
model.compile(loss="mean_squared_error",
    optimizer=opt,
    metrics=[rmse])

42


In [318]:
X_trainn

provider_Lyft  provider_Uber  ...  sin_time  cos_time
0                1.0            0.0  ...  0.910540  0.785407
3                1.0            0.0  ...  0.910540  0.785407
9                1.0            0.0  ...  0.910541  0.785406
10               1.0            0.0  ...  0.910541  0.785406
11               1.0            0.0  ...  0.910541  0.785406
...              ...            ...  ...       ...       ...
99988            1.0            0.0  ...  0.533570  0.998872
99989            1.0            0.0  ...  0.533572  0.998872
99990            1.0            0.0  ...  0.533572  0.998872
99991            1.0            0.0  ...  0.533572  0.998872
99993            1.0            0.0  ...  0.533572  0.998872

[48137 rows x 42 columns]

In [319]:
ytrain

0        34.0
3        10.5
9         7.0
10       47.5
11       62.5
         ... 
99988    27.5
99989    26.0
99990     5.0
99991     7.0
99993    13.5
Name: fare, Length: 48137, dtype: float64

In [320]:
!rm _model*

In [321]:
def scheduler(epoch, lr):
    return 0.0001

In [322]:
callback_LR = tf.keras.callbacks.LearningRateScheduler(scheduler)

In [323]:
callbacks = [callback_LR,
       
        ModelCheckpoint(filepath=fname+"_{val_root_mean_squared_error:.5f}__.hdf5", monitor='val_root_mean_squared_error',
                        verbose=2, save_best_only=True, mode='min')]

In [324]:
#modelname="_model_1__1.68411__.hdf5"
#model=tf.keras.models.load_model(modelname)

In [325]:
'''
modelname="_model_1__1.80573__.hdf5"
model=tf.keras.models.load_model(modelname)
'''

'\nmodelname="_model_1__1.80573__.hdf5"\nmodel=tf.keras.models.load_model(modelname)\n'

In [326]:
history = model.fit( X_trainn[0:-1],y_trainn[0:-1], 
                        epochs=555, 
                        batch_size=32,validation_split=0.2,
                        verbose=1,
                        callbacks=callbacks,shuffle=False,
                              
                              )

Epoch 1/555
1204/1204 [==============================] - 10s 8ms/step - loss: 123.0602 - root_mean_squared_error: 10.6921 - val_loss: 12.6257 - val_root_mean_squared_error: 3.5533

Epoch 00001: val_root_mean_squared_error improved from inf to 3.55326, saving model to _model_1__3.55326__.hdf5
Epoch 2/555
1204/1204 [==============================] - 9s 8ms/step - loss: 10.4555 - root_mean_squared_error: 3.2272 - val_loss: 8.5393 - val_root_mean_squared_error: 2.9222

Epoch 00002: val_root_mean_squared_error improved from 3.55326 to 2.92221, saving model to _model_1__2.92221__.hdf5
Epoch 3/555
1204/1204 [==============================] - 9s 8ms/step - loss: 8.6023 - root_mean_squared_error: 2.9289 - val_loss: 6.7210 - val_root_mean_squared_error: 2.5925

Epoch 00003: val_root_mean_squared_error improved from 2.92221 to 2.59250, saving model to _model_1__2.59250__.hdf5
Epoch 4/555
1204/1204 [==============================] - 10s 8ms/step - loss: 7.3571 - root_mean_squared_error: 2.7105 - v

KeyboardInterrupt: ignored

In [ ]:
#!rm _model*

In [ ]:
datag=pd.DataFrame()
y_pred=model.predict(Xtrain)



In [ ]:
datag["pred"]=list(y_pred.T[0])
datag["y"]=list(y_pred)
datag["delta"]=y_pred.T[0]-ytrain

In [ ]:
grafikon(datag,"pred","pred","delta","delta")

## betöltés

In [327]:
!pip install xgboost

In [ ]:
from sklearn.ensemble import GradientBoostingRegressor
from sklearn.datasets import make_regression
from sklearn.neural_network import MLPRegressor

#regr = GradientBoostingRegressor(n_estimators=100,max_depth=500, random_state=0)
#regr.fit(X_trainn, ytrain)

regr_Uber = MLPRegressor(random_state=1, max_iter=500,verbose=True,tol=1e-8)
regr_Uber.fit(X_train_Uber, y_train_Uber)



In [369]:

regr_Lyft = MLPRegressor(random_state=1, max_iter=500,verbose=True,tol=1e-8)
regr_Lyft.fit(X_train_Lyft, y_train_Lyft)



Iteration 1, loss = 75.96462166
Iteration 2, loss = 13.45336796
Iteration 3, loss = 4.82396923
Iteration 4, loss = 3.94494309
Iteration 5, loss = 3.27158767
Iteration 6, loss = 2.70629778
Iteration 7, loss = 2.32559912
Iteration 8, loss = 2.09315349
Iteration 9, loss = 1.94485781
Iteration 10, loss = 1.84543962
Iteration 11, loss = 1.77970538
Iteration 12, loss = 1.71357044
Iteration 13, loss = 1.66270676
Iteration 14, loss = 1.61361191
Iteration 15, loss = 1.57056130
Iteration 16, loss = 1.52521073
Iteration 17, loss = 1.48270215
Iteration 18, loss = 1.43928965
Iteration 19, loss = 1.39521991
Iteration 20, loss = 1.35637117
Iteration 21, loss = 1.31054079
Iteration 22, loss = 1.28200488
Iteration 23, loss = 1.25168645
Iteration 24, loss = 1.22564176
Iteration 25, loss = 1.20167456
Iteration 26, loss = 1.17927296
Iteration 27, loss = 1.16006376
Iteration 28, loss = 1.15009766
Iteration 29, loss = 1.13969722
Iteration 30, loss = 1.12854179
Iteration 31, loss = 1.11655899
Iteration 32, l

MLPRegressor(activation='relu', alpha=0.0001, batch_size='auto', beta_1=0.9,
             beta_2=0.999, early_stopping=False, epsilon=1e-08,
             hidden_layer_sizes=(100,), learning_rate='constant',
             learning_rate_init=0.001, max_fun=15000, max_iter=500,
             momentum=0.9, n_iter_no_change=10, nesterovs_momentum=True,
             power_t=0.5, random_state=1, shuffle=True, solver='adam',
             tol=1e-08, validation_fraction=0.1, verbose=True,
             warm_start=False)

In [ ]:
import xgboost as xgb
xgbr = xgb.XGBRegressor(n_estimators=300,   verbosity=2, max_depth=40) 
#print(xgbr)
xgbr.fit(X_trainn, ytrain,)

In [ ]:
score = xgbr.score(X_trainn, ytrain,)  
print("Training score: ", score)


In [ ]:
modelname="_model_1__1.67941__.hdf5"

In [ ]:
#!wget https://github.com/sipocz/CabPrice/raw/main/_model_1__1.64576__.hdf5

In [370]:
!wget https://github.com/sipocz/CabPrice/raw/B20210507/TEST.csv

--2021-05-22 14:26:31--  https://github.com/sipocz/CabPrice/raw/B20210507/TEST.csv
Resolving github.com (github.com)... 140.82.112.4
Connecting to github.com (github.com)|140.82.112.4|:443... connected.
HTTP request sent, awaiting response... 302 Found
Location: https://raw.githubusercontent.com/sipocz/CabPrice/B20210507/TEST.csv [following]
--2021-05-22 14:26:31--  https://raw.githubusercontent.com/sipocz/CabPrice/B20210507/TEST.csv
Resolving raw.githubusercontent.com (raw.githubusercontent.com)... 185.199.108.133, 185.199.109.133, 185.199.110.133, ...
Connecting to raw.githubusercontent.com (raw.githubusercontent.com)|185.199.108.133|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 1757163 (1.7M) [text/plain]
Saving to: ‘TEST.csv’

TEST.csv            100%[===================>]   1.67M  --.-KB/s    in 0.03s   

2021-05-22 14:26:32 (58.0 MB/s) - ‘TEST.csv’ saved [1757163/1757163]



In [ ]:


model=tf.keras.models.load_model(modelname)

In [371]:
dft=pd.read_csv("TEST.csv")

In [372]:
dft.head()

index     time_stamp cab_provider  ... distance surge_multiplier      cab_type
0      0  1543364124206         Lyft  ...     0.59              1.0           Lux
1      1  1543364124206         Lyft  ...     0.59              1.0  Lux Black XL
2      2  1543364124206         Uber  ...     6.83              1.0         UberX
3      3  1543364124206         Uber  ...     1.35              1.0        UberXL
4      4  1543364124206         Lyft  ...     0.59              1.0       Lyft XL

[5 rows x 8 columns]

In [373]:
dft.tail()

index     time_stamp cab_provider  ... distance surge_multiplier   cab_type
24995  24995  1543413683462         Uber  ...     3.05              1.0   UberPool
24996  24996  1543413683462         Uber  ...     3.05              1.0        WAV
24997  24997  1543413683462         Uber  ...     3.05              1.0  Black SUV
24998  24998  1543413683687         Lyft  ...     2.96              1.0     Shared
24999  24999  1543413683687         Lyft  ...     2.96              1.0        Lux

[5 rows x 8 columns]

In [374]:

X_test=DataPipeLine(dft,startup=False)

In [375]:
X_test.head()

provider_Lyft  provider_Uber  ...  sin_time  cos_time
0            1.0            0.0  ...   0.53358  0.998871
1            1.0            0.0  ...   0.53358  0.998871
2            0.0            1.0  ...   0.53358  0.998871
3            0.0            1.0  ...   0.53358  0.998871
4            1.0            0.0  ...   0.53358  0.998871

[5 rows x 42 columns]

In [377]:
remover=X_test[X_test.provider_Uber==1].index
X_test_Lyft=X_test.drop(remover, inplace=False)

remover=X_test[X_test.provider_Lyft==1].index
X_test_Uber=X_test.drop(remover, inplace=False)





In [378]:
y_test_Lyft=regr_Lyft.predict(X_test_Lyft)


In [382]:
y_test_Uber=regr_Uber.predict(X_test_Uber)

In [384]:
y_test_Uber

array([16.62130312, 13.36863577, 15.76453295, ..., 10.08758464,
       10.456394  , 32.89074753])

In [388]:
df_Uber=pd.DataFrame(y_test_Uber,index=X_test_Uber.index)

In [390]:
df_Uber.head()

0
2   16.621303
3   13.368636
12  15.764533
21  30.743241
23  10.438529

In [391]:
df_Lyft=pd.DataFrame(y_test_Lyft,index=X_test_Lyft.index)

In [394]:
df_all=df_Lyft.append(df_Uber)

In [396]:
df_all.sort_index()

0
0      10.962380
1      27.031478
2      16.621303
3      13.368636
4      10.218087
...          ...
24995  10.087585
24996  10.456394
24997  32.890748
24998   6.893718
24999  20.285729

[25000 rows x 1 columns]

In [ ]:
y_regr

In [ ]:
y_regr

In [ ]:
odf=pd.DataFrame(y_test)

In [ ]:
odf.head()

In [ ]:
!wget https://github.com/sipocz/CabPrice/raw/B20210507/sample_submission.csv

In [ ]:
!head sample_submission.csv

In [ ]:
def round_half(a):
    return(a)
    import math
    e=math.floor(a)
    m=a-e
    if m>0.75:
        return e+1
    if m<0.25:
        return e
    return e+0.5

In [ ]:
odf.columns=["fare2"]
odf.index.name="index"
odf["fare"]=odf["fare2"].apply(lambda x:round_half(x))


In [ ]:
del odf["fare2"] #drop(['algebra', 'chemistry'], axis=1)
odf.head()

In [ ]:
odf.to_csv("submission_17_1.67941.csv")

In [ ]:
! head submission_17_1.67941.csv